#### DataFrames are built on top of RDD's and provide database type functionality
#### We will use some sample data from Wegmans to explore DataFrames
#### First let's look at the textfile with the store data

### A SparkSession gets creted automatically and is assigned to variable 'spark'. It also creates a SparkContext 'sc' if it does not exist already

In [64]:
spark

In [65]:
sc

In [66]:
path='/public/tbiswas2/csc261/spark/wegmans/'
storeRDD=sc.textFile(path+'wegmans_store_master.txt')
storeRDD.take(5)

[u'80|WEGMANS DICK ROAD|BUFFALO|DEPEW|NY|1',
 u'82|WEGMANS ALBERTA DRIVE|BUFFALO|AMHERST|NY|1',
 u'83|WEGMANS SHERIDAN DRIVE|BUFFALO|WILLIAMSVILLE|NY|1',
 u'84|WEGMANS MCKINLEY|BUFFALO|BUFFALO|NY|1',
 u'86|WEGMANS NIAGARA FALLS BLV|BUFFALO|AMHERST|NY|1']

#### The data is pipe delimited and contains the store number, name, zone, city, state, and type
#### To turn this textual data into a columnar dataset, we can use the Row datatype

In [67]:
from pyspark.sql import Row
Row(id=1,fname='Biswas',lname='Tamal')

Row(fname='Biswas', id=1, lname='Tamal')

#### We need to define a function that can turn a RDD containing lines of text into RDD's contain Rows with labeled columns for the store data

In [68]:
from pyspark.sql import Row
def parseStore(s):
    l=s.split('|')
    return Row(store_num=int(l[0]), 
               store_name=l[1],               
               store_zone=l[2],
               store_city=l[3], 
               store_state=l[4], 
               store_type=int(l[5]))

#### Now we can transform our RDD containing strings, to one containing rows

In [69]:
storeRowRDD=storeRDD.map(lambda x: parseStore(x))
storeRowRDD.first()

Row(store_city=u'DEPEW', store_name=u'WEGMANS DICK ROAD', store_num=80, store_state=u'NY', store_type=1, store_zone=u'BUFFALO')

In [70]:
type(storeRowRDD)

pyspark.rdd.PipelinedRDD

#### Now we can take our RDD of Rows and turn it into a DataFrame

In [71]:
storeDF=spark.createDataFrame(storeRowRDD)
type(storeDF)

pyspark.sql.dataframe.DataFrame

#### Data frames support additional actions and transformations

In [72]:
storeDF.take(5)

[Row(store_city=u'DEPEW', store_name=u'WEGMANS DICK ROAD', store_num=80, store_state=u'NY', store_type=1, store_zone=u'BUFFALO'),
 Row(store_city=u'AMHERST', store_name=u'WEGMANS ALBERTA DRIVE', store_num=82, store_state=u'NY', store_type=1, store_zone=u'BUFFALO'),
 Row(store_city=u'WILLIAMSVILLE', store_name=u'WEGMANS SHERIDAN DRIVE', store_num=83, store_state=u'NY', store_type=1, store_zone=u'BUFFALO'),
 Row(store_city=u'BUFFALO', store_name=u'WEGMANS MCKINLEY', store_num=84, store_state=u'NY', store_type=1, store_zone=u'BUFFALO'),
 Row(store_city=u'AMHERST', store_name=u'WEGMANS NIAGARA FALLS BLV', store_num=86, store_state=u'NY', store_type=1, store_zone=u'BUFFALO')]

#### Data Frames support pretty output using show instead of take

In [73]:
storeDF.show(5)

+-------------+--------------------+---------+-----------+----------+----------+
|   store_city|          store_name|store_num|store_state|store_type|store_zone|
+-------------+--------------------+---------+-----------+----------+----------+
|        DEPEW|   WEGMANS DICK ROAD|       80|         NY|         1|   BUFFALO|
|      AMHERST|WEGMANS ALBERTA D...|       82|         NY|         1|   BUFFALO|
|WILLIAMSVILLE|WEGMANS SHERIDAN ...|       83|         NY|         1|   BUFFALO|
|      BUFFALO|    WEGMANS MCKINLEY|       84|         NY|         1|   BUFFALO|
|      AMHERST|WEGMANS NIAGARA F...|       86|         NY|         1|   BUFFALO|
+-------------+--------------------+---------+-----------+----------+----------+
only showing top 5 rows



#### You can view the schema of your dataframe

In [74]:
storeDF.printSchema()

root
 |-- store_city: string (nullable = true)
 |-- store_name: string (nullable = true)
 |-- store_num: long (nullable = true)
 |-- store_state: string (nullable = true)
 |-- store_type: long (nullable = true)
 |-- store_zone: string (nullable = true)



#### And select certain columns
(Don't get confused by the name. It actually does projection)<br>
Two (2) ways of doing it. 

In [75]:
storeDF.select("store_name").show()

+--------------------+
|          store_name|
+--------------------+
|   WEGMANS DICK ROAD|
|WEGMANS ALBERTA D...|
|WEGMANS SHERIDAN ...|
|    WEGMANS MCKINLEY|
|WEGMANS NIAGARA F...|
| WEGMANS LOSSON ROAD|
| WEGMANS WEST SENECA|
| WEGMANS TRANSIT RD.|
|  WEGMANS AMHERST ST|
|WEGMANS MILITARY ...|
|   WEGMANS ERIE WEST|
|        WEGMANS ERIE|
|   WEGMANS JAMESTOWN|
|   WEGMANS ALLENTOWN|
|    WEGMANS NAZARETH|
|   WEGMANS BETHLEHEM|
| WEGMANS HUNT VALLEY|
|    WEGMANS WOODMORE|
|    WEGMANS COLUMBIA|
|     WEGMANS BEL AIR|
+--------------------+
only showing top 20 rows



#### The other way of projection

In [76]:
storeDF.select(storeDF['store_name']).show()

+--------------------+
|          store_name|
+--------------------+
|   WEGMANS DICK ROAD|
|WEGMANS ALBERTA D...|
|WEGMANS SHERIDAN ...|
|    WEGMANS MCKINLEY|
|WEGMANS NIAGARA F...|
| WEGMANS LOSSON ROAD|
| WEGMANS WEST SENECA|
| WEGMANS TRANSIT RD.|
|  WEGMANS AMHERST ST|
|WEGMANS MILITARY ...|
|   WEGMANS ERIE WEST|
|        WEGMANS ERIE|
|   WEGMANS JAMESTOWN|
|   WEGMANS ALLENTOWN|
|    WEGMANS NAZARETH|
|   WEGMANS BETHLEHEM|
| WEGMANS HUNT VALLEY|
|    WEGMANS WOODMORE|
|    WEGMANS COLUMBIA|
|     WEGMANS BEL AIR|
+--------------------+
only showing top 20 rows



#### And filter on various criteria

In [77]:
storeDF.filter(storeDF['store_zone']=='ROCHESTER').show()

+-----------+--------------------+---------+-----------+----------+----------+
| store_city|          store_name|store_num|store_state|store_type|store_zone|
+-----------+--------------------+---------+-----------+----------+----------+
|    WEBSTER|     WEGMANS EASTWAY|        3|         NY|         1| ROCHESTER|
|   FAIRPORT|    WEGMANS FAIRPORT|        4|         NY|         1| ROCHESTER|
|     NEWARK|      WEGMANS NEWARK|        6|         NY|         1| ROCHESTER|
|CANANDAIGUA| WEGMANS CANANDAIGUA|       11|         NY|         1| ROCHESTER|
|  ROCHESTER|   WEGMANS RIDGEMONT|       12|         NY|         1| ROCHESTER|
|  ROCHESTER|WEGMANS LYELL AVENUE|       13|         NY|         1| ROCHESTER|
|  ROCHESTER| WEGMANS EAST AVENUE|       18|         NY|         1| ROCHESTER|
|  ROCHESTER|WEGMANS RIDGE-CULVER|       19|         NY|         1| ROCHESTER|
|  ROCHESTER|    WEGMANS MT. READ|       20|         NY|         1| ROCHESTER|
|  ROCHESTER|WEGMANS CALKINS ROAD|       22|        

In [78]:
storeDF.filter(storeDF['store_zone']=='ROCHESTER').select(storeDF['store_name']).show()

+--------------------+
|          store_name|
+--------------------+
|     WEGMANS EASTWAY|
|    WEGMANS FAIRPORT|
|      WEGMANS NEWARK|
| WEGMANS CANANDAIGUA|
|   WEGMANS RIDGEMONT|
|WEGMANS LYELL AVENUE|
| WEGMANS EAST AVENUE|
|WEGMANS RIDGE-CULVER|
|    WEGMANS MT. READ|
|WEGMANS CALKINS ROAD|
|    WEGMANS PERINTON|
|   WEGMANS PITTSFORD|
|     WEGMANS GENESEO|
| WEGMANS MARKETPLACE|
|    WEGMANS PENFIELD|
|  WEGMANS LATTA ROAD|
|   WEGMANS BROCKPORT|
|   WEGMANS HOLT ROAD|
| WEGMANS IRONDEQUOIT|
|  WEGMANS CHILI-PAUL|
+--------------------+
only showing top 20 rows



#### Or group by various criteria

In [79]:
storeDF.groupBy('store_zone').count().show()

+-------------+-----+
|   store_zone|count|
+-------------+-----+
|   NEW JERSEY|   12|
| PENNSYLVANIA|    5|
|     MARYLAND|    8|
|    ROCHESTER|   23|
|  NEW ENGLAND|    2|
|     VIRGINIA|    6|
|LEHIGH VALLEY|    3|
|      BUFFALO|   10|
|SOUTHERN TIER|    6|
|     SYRACUSE|   10|
|         ERIE|    2|
|    JAMESTOWN|    1|
| SOUTHEAST PA|    6|
+-------------+-----+



#### You can also create temporary tables for use with SQL statements
### We will not use this approach (Basic SQL is for kids!)

In [80]:
storeDF.createOrReplaceTempView('store')

In [81]:
result=spark.sql("select store_zone, COUNT(store_zone) as num_stores from store GROUP BY store_zone ORDER BY num_stores DESC")

#### SQL queries return data frame objects

In [82]:
type(result)

pyspark.sql.dataframe.DataFrame

In [83]:
result.show(5)

+----------+----------+
|store_zone|num_stores|
+----------+----------+
| ROCHESTER|        23|
|NEW JERSEY|        12|
|  SYRACUSE|        10|
|   BUFFALO|        10|
|  MARYLAND|         8|
+----------+----------+
only showing top 5 rows



#### Now we can create RDDs from the 3 other text files containing information on items, customers, and transactions

In [84]:
itemRDD=sc.textFile(path+'wegmans_item_master.txt')
customerRDD=sc.textFile(path+'wegmans_customer_master.txt')
postransRDD=sc.textFile(path+'partial_transaction.dat')

#### The item data contains information about the item including its name, department, size, etc...

In [85]:
itemRDD.first()

u'19190|010101|WG GIANT BREAD|22.000|OZ|WEGF|1|BAKESHOP|1|WEGMANS WHITE BREADS|1|WEGMAN WHITE BREAD'

#### The customer data contains information on each household including the birth year of the head of household, the household income, size, number of adults, children and there age range.

In [86]:
customerRDD.first()

u'559|1981|62500|2|2|0|0|0|N|N|2012-10-21|0|0|0'

#### And the transaction database contains information about each item purchase

In [87]:
postransRDD.first()

u'559|559|174758|2013-06-01|64|16705|010327|1|1.99|1.99|0.00'

#### We need to import datetime to parse the dates in the text file

In [88]:
from datetime import datetime

#### And create functions to parse a line of text from each of the three files into Row RDD's

In [89]:
# Define functions to parse txt files containing itmes, stores, customers, and transactions
def parseItem(s):
    l=s.split('|')
    return Row(item_number=int(l[0]), 
               dept_categ_class=l[1],               
               item_des=l[2],
               item_unt_qty=float(l[3]), 
               size_unit_desc=l[4], 
               brand_code=l[5], 
               dept_num=int(l[6]), 
               dept_name=l[7], 
               categ_num=int(l[8]), 
               categ_name=l[9], 
               class_num=int(l[10]),
               class_name=l[11])
def parseCustomer(s):
    l=s.split('|')
    return Row(hshld_acct=int(l[0]),
               birth_yr_head_hh=l[1],
               hh_income=l[2],
               hh_size=l[3],
               adult_count=l[4],
               child_count=l[5],
               birth_yr_oldest=l[6],
               birth_yr_youngest=l[7],
               bad_address=l[8],
               privacy=l[9],
               application_date=datetime.strptime(l[10],'%Y-%m-%d'),
               wine_email_sent=int(l[11]),
               wine_email_open=int(l[12]),
               wine_email_click=int(l[13]))
def parsePostrans(s):
    l=s.split('|')
    return Row(hshld_acct=int(l[0]),
               acct_num=int(l[1]),
               trans_num=int(l[2]),
               trans_date=datetime.strptime(l[3],'%Y-%m-%d'),
               store_num=int(l[4]),
               item_number=int(l[5]),
               dept_categ_class=l[6],
               unit_count=int(l[7]),
               net_sales=float(l[8]),
               gross_sales=float(l[9]),
               manuf_coupon=float(l[10]))


#### We then can create Row RDD's using maps of the text RDD's

In [90]:
itemRowRDD=itemRDD.map(lambda x: parseItem(x))
customerRowRDD=customerRDD.map(lambda x: parseCustomer(x))
postransRowRDD=postransRDD.map(lambda x: parsePostrans(x))

In [91]:
customerRowRDD.first()

Row(adult_count=u'2', application_date=datetime.datetime(2012, 10, 21, 0, 0), bad_address=u'N', birth_yr_head_hh=u'1981', birth_yr_oldest=u'0', birth_yr_youngest=u'0', child_count=u'0', hh_income=u'62500', hh_size=u'2', hshld_acct=559, privacy=u'N', wine_email_click=0, wine_email_open=0, wine_email_sent=0)

#### And then create DataFrames for each of the Row RDD's

In [92]:
itemDF=spark.createDataFrame(itemRowRDD)
customerDF=spark.createDataFrame(customerRowRDD)
postransDF=spark.createDataFrame(postransRowRDD)

In [93]:
customerDF.select("adult_count","child_count","hh_income").show(10)

+-----------+-----------+---------+
|adult_count|child_count|hh_income|
+-----------+-----------+---------+
|          2|          0|    62500|
|          0|          0|        0|
|          2|          1|   112500|
|          1|          0|    35000|
|          0|          0|        0|
|          1|          0|    35000|
|          4|          0|   150000|
|          1|          0|    10000|
|          0|          0|        0|
|          0|          0|        0|
+-----------+-----------+---------+
only showing top 10 rows



In [94]:
customerDF.describe().show();

+-------+------------------+-------------------+------------------+------------------+
|summary|        hshld_acct|   wine_email_click|   wine_email_open|   wine_email_sent|
+-------+------------------+-------------------+------------------+------------------+
|  count|             49506|              49506|             49506|             49506|
|   mean| 4766311.056881994|0.04692360521956934|0.7600492869551165|1.9953136993495737|
| stddev|2685918.2614031075| 0.9132672634762621| 5.888460304759305|10.914263956720259|
|    min|               559|                  0|                 0|                 0|
|    max|         100001200|                 63|               149|                65|
+-------+------------------+-------------------+------------------+------------------+



#### Now we can use DataFrame operations to group transactions by store number, aggregate the result, and then join the result against the store dataframe and print out the total sales for each store name sorted by total sales in descending order.

In [95]:
# Need to import aggregate functions
from pyspark.sql import functions as F

In [96]:
postransDF.groupBy('store_num').max('unit_count').show()

+---------+---------------+
|store_num|max(unit_count)|
+---------+---------------+
|       26|             36|
|       65|              9|
|       19|             31|
|       22|            132|
|       34|              4|
|       84|              7|
|       31|              2|
|       39|              4|
|       25|             64|
|       71|              8|
|       68|             24|
|        6|             20|
|       87|              5|
|       63|             25|
|       51|              5|
|       17|              6|
|       33|              2|
|       88|              8|
|        1|              3|
|       89|              8|
+---------+---------------+
only showing top 20 rows



In [97]:
postransDF.groupBy('store_num') \
          .agg(F.sum('gross_sales').alias('total_sales')) \
          .join(storeDF, 'store_num') \
          .select('store_name','total_sales') \
          .sort('total_sales',ascending=False) \
          .show()

+--------------------+------------------+
|          store_name|       total_sales|
+--------------------+------------------+
|   WEGMANS PITTSFORD|1053008.8199995044|
|     WEGMANS EASTWAY| 556006.2699999192|
|   WEGMANS HOLT ROAD|521012.02999990876|
|    WEGMANS PERINTON| 458570.2999999707|
| WEGMANS EAST AVENUE| 412401.9299999929|
|    WEGMANS PENFIELD| 306910.2900000174|
|CENTURY LIQUOR AN...| 275641.9000000139|
|WEGMANS CALKINS ROAD|166491.43000000733|
|    WEGMANS FAIRPORT|126287.79999999909|
|WEGMANS RIDGE-CULVER| 118673.0099999988|
| WEGMANS IRONDEQUOIT|117386.63999999785|
|WEGMANS LYELL AVENUE|  96316.9300000009|
| WEGMANS MARKETPLACE| 87086.24000000117|
|    WEGMANS MT. READ| 79793.92000000403|
|  WEGMANS LATTA ROAD| 78244.66000000214|
|   WEGMANS RIDGEMONT| 72789.00000000303|
| WEGMANS CANANDAIGUA| 65537.71000000079|
|      WEGMANS GENEVA| 63871.47000000156|
|  WEGMANS CHILI-PAUL| 56436.59000000395|
|      WEGMANS NEWARK| 40034.00000000071|
+--------------------+------------

#### We could also create temporary tables and use traditional SQL statements.
## Again, we won't use this approach

In [98]:
itemDF.createOrReplaceTempView('item')
customerDF.createOrReplaceTempView('customer')
postransDF.createOrReplaceTempView('postrans')

In [99]:
#Create an SQL transformation that finds the top 20 stores
bigstores = spark.sql("SELECT store.store_name, SUM(postrans.gross_sales) AS total_sales " 
                           "FROM postrans "
                           "INNER JOIN store ON postrans.store_num=store.store_num "
                           "GROUP BY store.store_name "
                           "ORDER BY total_sales DESC")

In [100]:
#Run the action
bigstores.show()

+--------------------+------------------+
|          store_name|       total_sales|
+--------------------+------------------+
|   WEGMANS PITTSFORD| 1053008.819999029|
|     WEGMANS EASTWAY| 556006.2699995728|
|   WEGMANS HOLT ROAD|521012.02999964607|
|    WEGMANS PERINTON| 458570.2999997144|
| WEGMANS EAST AVENUE|412401.92999976495|
|    WEGMANS PENFIELD|306910.28999991383|
|CENTURY LIQUOR AN...|275641.89999997016|
|WEGMANS CALKINS ROAD|166491.43000000253|
|    WEGMANS FAIRPORT|126287.80000001815|
|WEGMANS RIDGE-CULVER|118673.01000001446|
| WEGMANS IRONDEQUOIT|117386.64000001612|
|WEGMANS LYELL AVENUE| 96316.93000000803|
| WEGMANS MARKETPLACE|  87086.2400000054|
|    WEGMANS MT. READ| 79793.92000000279|
|  WEGMANS LATTA ROAD|  78244.6600000007|
|   WEGMANS RIDGEMONT|  72789.0000000003|
| WEGMANS CANANDAIGUA|  65537.7099999975|
|      WEGMANS GENEVA| 63871.46999999698|
|  WEGMANS CHILI-PAUL| 56436.58999999898|
|      WEGMANS NEWARK| 40034.00000000184|
+--------------------+------------

#### Now for fun, let's look at the average household income of shoppers at each of the stores

In [101]:
print (postransDF.join(customerDF, 'hshld_acct').count())


1153915


In [102]:
postransDF.describe('store_num').show()

+-------+-----------------+
|summary|        store_num|
+-------+-----------------+
|  count|          1153915|
|   mean|31.97120671799916|
| stddev|23.87778749839352|
|    min|                1|
|    max|              162|
+-------+-----------------+



In [103]:
postransDF.join(customerDF, 'hshld_acct') \
    .filter(customerDF.hshld_acct>0).count();

In [104]:
postransDF.join(customerDF, 'hshld_acct') \
    .filter(customerDF.hshld_acct>0) \
    .groupBy('store_num') \
    .agg(F.avg('hh_income').alias('average household income')) \
    .join(storeDF, 'store_num') \
    .select('store_name','average household income') \
    .sort('average household income',ascending=False) \
    .show(100)

+--------------------+------------------------+
|          store_name|average household income|
+--------------------+------------------------+
|      WEGMANS AUBURN|      138117.64705882352|
|      WEGMANS ITHACA|      132877.85171102663|
|    WEGMANS ONONDAGA|                129000.0|
| WEGMANS LOSSON ROAD|      117483.97435897436|
|JOHNSON CITY LIQU...|                112500.0|
|  WEGMANS AMHERST ST|      112297.67628205128|
| WEGMANS CANANDAIGUA|      104870.76707395498|
|   WEGMANS HOLT ROAD|        91897.9953349177|
|   WEGMANS BROCKPORT|       91389.42307692308|
|     WEGMANS GENESEO|       89562.71216723244|
|WEGMANS ALBERTA D...|         89293.893129771|
|    WEGMANS PENFIELD|       88015.79225468541|
|     WEGMANS EASTWAY|       87585.14284924463|
|    WEGMANS FAIRPORT|       84467.75723091513|
|CENTURY LIQUOR AN...|       83341.29480822517|
|    WEGMANS PERINTON|       82797.74124422538|
|   WEGMANS PITTSFORD|       81660.89511052189|
|   WEGMANS FAIRMOUNT|        80028.7356

In [105]:
# Market-Basket Model
# Need to create an RDD containing lists of items corresponding to each shopping cart - or transaction

# First we create a dataframe containing the transaction numbers and item_description
basketsDF=postransDF.join(itemDF,'item_number').select('trans_num','item_des')
basketsDF.show(5)

+---------+--------------------+
|trans_num|            item_des|
+---------+--------------------+
|143732868|R/S MARSHMALLOW E...|
|154654547|R/S MARSHMALLOW E...|
|152337781|R/S MARSHMALLOW E...|
|148124225|R/S MARSHMALLOW E...|
|129604411|R/S MARSHMALLOW E...|
+---------+--------------------+
only showing top 5 rows



In [106]:
# Next we need to create a mapped RDD with the transaction number as the key and the item as the value
# When we call the map operation on a DataFrame, it returns a Row object which supports referencing elements by name
basketRDD=basketsDF.rdd

In [107]:
baskets=basketRDD.groupByKey().map(lambda x: list(set(x[1])))

In [108]:
baskets.take(5)

[[u'WEG MILK FAT FREE',
  u'CHS/SAUS/SPIC RONI PIE-PK',
  u'BUFFALO CKN WINGS-PKG'],
 [u'OC SPRAY 100% CRAN JUICE',
  u'ASPARAGUS, 28 LB',
  u'WEGMANS REG MARSHMALLOWS',
  u'HER REESE PBC MINI',
  u'WEG ULTRA HALF & HALF',
  u'WB ORIGINAL HUMMUS FP',
  u'WEG INSTANT RICE',
  u'WEG MILK 2% LOWFAT',
  u'STRAWBERRIES, 2LBS',
  u'HK AND PRETZL STK BARREL',
  u'MT DEW 12PK 12OZ',
  u'CHEEZ-IT ORG CHSE CRKR',
  u'CHEEZ-IT WHT CHEDDAR CRKR',
  u'WEG 2# LEMONS',
  u'WB ORG SPRING MIX 16OZ',
  u'COKE ZERO       6/16.9 BT',
  u'WEG CRISP RICE'],
 [u'BQT-PETITE (20 ST)',
  u'AG EVERYDAY GREETING CARD',
  u'MUM 4.5 WOW',
  u'AG EVERYDAY CARD'],
 [u'AG EVERYDAY GREETING CARD'],
 [u'COCA-COLA ZERO      20 OZ',
  u'HER BS WINTERGREEN',
  u'WEG INST LIGHT CHARC BRIQ',
  u'SUB SHOP WRAPS']]

In [109]:
# Now we can setup the FP-Growth model and calculate frequent item sets
from pyspark.mllib.fpm import FPGrowth
model = FPGrowth.train(baskets, minSupport=0.005, numPartitions=10)
result = model.freqItemsets().collect()

In [110]:
# Now we can loop over 
for fi in sorted(result, key=lambda x: x.freq, reverse=True)[0:50]:
    print(fi)

FreqItemset(items=[u'BANANAS           T6H8'], freq=18125)
FreqItemset(items=[u'WEG MILK FAT FREE'], freq=6095)
FreqItemset(items=[u'WEG GRADE AA LARGE EGGS'], freq=5684)
FreqItemset(items=[u'BROCCOLI CROWNS'], freq=4875)
FreqItemset(items=[u'RED SEEDLESS GRAPES'], freq=4161)
FreqItemset(items=[u'SELF SERVE OLIVE BAR'], freq=3916)
FreqItemset(items=[u'WEGMAN 1# BABYCUTS'], freq=3532)
FreqItemset(items=[u'BULK ROLLS'], freq=3431)
FreqItemset(items=[u'WEG MILK 2% LOWFAT'], freq=3306)
FreqItemset(items=[u'WEG MILK 1% LOWFAT'], freq=3257)
FreqItemset(items=[u'LEMONS BULK'], freq=3098)
FreqItemset(items=[u'I/S BAGELS'], freq=3032)
FreqItemset(items=[u'36CT SEEDED CUKES'], freq=2864)
FreqItemset(items=[u'WEG BUTTER,STICKS'], freq=2851)
FreqItemset(items=[u'AVOCADO SINGLE LAYER'], freq=2746)
FreqItemset(items=[u'STRAWBERRIES, 2LBS'], freq=2710)
FreqItemset(items=[u'STRAWBERRIES, 1LB'], freq=2684)
FreqItemset(items=[u'CELERY, SMALL (36 CT)'], freq=2612)
FreqItemset(items=[u'TOM, RED ON VINE'],

#### Association Rules
Now once we have these FreqItemSets, we can ask questions like 
*  *How likely is it that someone will buy bananas (Support)*
*  *How likely is it that someone will buy milk given that they by bananas (Confidence)*
*  *How much more likely is it that someone will buy milk, given that they are also buying bananas? (Lift)*

This can be calculated using conditional probabilities:
* A = 'Person bought bananas'
* B = 'Person bought milk'

$P(A)$

$P(B|A) = P(B \cap A)/P(A)$

$P(B|A)/P(B)=P(B\cap A)/(P(A)P(B))$



In [111]:
def association(result,item1,item2,N):
    X=[fi.freq for fi in result if set(fi.items)==item1][0]
    Y=[fi.freq for fi in result if set(fi.items)==item2][0]
    X_and_Y=[fi.freq for fi in result if set(fi.items)==item1.union(item2)]
    if len(X_and_Y)>0:
        X_and_Y=X_and_Y[0]
    else:  #assume uncorrelated
        X_and_Y=X*Y/N/N
    support=float(X)/N
    confidence=float(X_and_Y)/X
    lift=confidence/(float(Y)/N)
    return (support, confidence, lift)
    

In [112]:
item1=set(['BANANAS           T6H8'])
item2=set(['WEG MILK FAT FREE'])
N=baskets.count()
(support, confidence, lift)=association(result,item1,item2,N)

print('support = ' + str(support))
print('confidence = ' + str(confidence))
print('lift = ' + str(lift))

support = 0.190069211409
confidence = 0.134344827586
lift = 2.10190693333


Here we've considered the association rule that 'BANANAS' => 'WEG MILK FAT FREE'

* There are 18,125 baskets out of 95,360 that have bananas, so the support of the association rule is 19%.
* The confidence of the rule is the number of baskets that also contain milk divided by the number of baskets that
contain bananas = 2,435 / 18,125 = 13.4%
* The chance that a basket has fat free milk is only 6,095/ 95,360 or 6.4%
* So the lift (predictive usefulness) of the rule is 13.4/6.4=2.1


In [113]:
items=[set(fi.items) for fi in result]
rules=[]
for i in range(0,len(items)):
    for j in range(i+1,len(items)):
        if bool(items[i] & items[j]):
            continue
        (support,confidence,lift)=association(result,items[i],items[j],N)
        if lift > 1:
            rules.append((items[i],items[j],support,confidence,lift))


In [114]:
sorted(rules, key=lambda x: -x[4])[0:200]

[({u'LEMONS BULK'},
  {u'FRESH LIMES'},
  0.03248741610738255,
  0.18850871530019367,
  9.491125180056214),
 ({u'BROCCOLI CROWNS'},
  {u'WEGMAN 1# BABYCUTS'},
  0.05112206375838926,
  0.12102564102564102,
  3.267555245811191),
 ({u'WEG GRADE AA LARGE EGGS'},
  {u'WEG BUTTER,STICKS'},
  0.059605704697986574,
  0.09289232934553132,
  3.1070545515222263),
 ({u'WEG GRADE AA LARGE EGGS'},
  {u'WEG MILK 1% LOWFAT'},
  0.059605704697986574,
  0.10116115411681914,
  2.961844536868245),
 ({u'BANANAS           T6H8'},
  {u'WEG RASPBERRY GREEK YGT'},
  0.19006921140939598,
  0.03255172413793103,
  2.8142632944633754),
 ({u'BANANAS           T6H8'},
  {u'WEG BLK CHRY GREEK YOGURT'},
  0.19006921140939598,
  0.032275862068965516,
  2.8056756671800835),
 ({u'BROCCOLI CROWNS'},
  {u'RED SEEDLESS GRAPES'},
  0.05112206375838926,
  0.11897435897435897,
  2.726602949241738),
 ({u'BANANAS           T6H8'},
  {u'CLEMENTINES 2#'},
  0.19006921140939598,
  0.03481379310344827,
  2.5895813653235784),
 ({u'WE